# Subject4: Latency and capacity estimation for a network connection from asymmetric measurements

In [3]:
%matplotlib inline
import matplotlib.pyplot as plt
import pandas as pd
import isoweek
from os import path
import urllib.request as request
import gzip as gz
import shutil
import re
from collections import OrderedDict

## Data

In [4]:
def download_decompress_file(url, filename) :
    if not path.exists(filename) :
        print("No local data copy available for " + filename + ", creating new version")
        #request.urlretrieve(url, archive)
        request.urlretrieve(url, filename)
        #with gz.open(archive, 'rb') as f_in:
        #    with open(filename, 'wb') as f_out:
        #        shutil.copyfile(f_in, f_out)
        #print("New local copy created")
    else :
        print("Using local version of " + filename)

First data to examine, ping traces from on-campus connection.
We first check if a local copy of the data exists. If no copy is available, a new archive is downloaded then decompressed.

In [5]:
liglab2_url = "http://mescal.imag.fr/membres/arnaud.legrand/teaching/2014/RICM4_EP_ping/liglab2.log.gz"
liglab2_file = "liglab2.log.gz"

download_decompress_file(liglab2_url, liglab2_file)

Using local version of liglab2.log.gz


Second data to examine, ping traces from stackoverflow. As before, we download and decompress the file if a local copy doesn't already exist.

In [6]:
stackoverflow_url = "http://mescal.imag.fr/membres/arnaud.legrand/teaching/2014/RICM4_EP_ping/stackoverflow.log.gz"
stackoverflow_file = "stackoverflow.log"

download_decompress_file(stackoverflow_url, stackoverflow_file)

Using local version of stackoverflow.log


## 1st dataset: Liglab2

In [7]:
with gz.open(liglab2_file, 'rt') as f_in:
    file_content = f_in.read().split("\n")

In [8]:
file_content

['[1421761682.052172] 665 bytes from lig-publig.imag.fr (129.88.11.7): icmp_seq=1 ttl=60 time=22.5 ms',
 '[1421761682.277315] 1373 bytes from lig-publig.imag.fr (129.88.11.7): icmp_seq=1 ttl=60 time=21.2 ms',
 '[1421761682.502054] 262 bytes from lig-publig.imag.fr (129.88.11.7): icmp_seq=1 ttl=60 time=21.2 ms',
 '[1421761682.729257] 1107 bytes from lig-publig.imag.fr (129.88.11.7): icmp_seq=1 ttl=60 time=23.3 ms',
 '[1421761682.934648] 1128 bytes from lig-publig.imag.fr (129.88.11.7): icmp_seq=1 ttl=60 time=1.41 ms',
 '[1421761683.160397] 489 bytes from lig-publig.imag.fr (129.88.11.7): icmp_seq=1 ttl=60 time=21.9 ms',
 '[1421761683.443055] 1759 bytes from lig-publig.imag.fr (129.88.11.7): icmp_seq=1 ttl=60 time=78.7 ms',
 '[1421761683.672157] 1146 bytes from lig-publig.imag.fr (129.88.11.7): icmp_seq=1 ttl=60 time=25.1 ms',
 '[1421761683.899933] 884 bytes from lig-publig.imag.fr (129.88.11.7): icmp_seq=1 ttl=60 time=24.0 ms',
 '[1421761684.122687] 1422 bytes from lig-publig.imag.fr (1

In [11]:
list = []
reg = [('timestamp',r'\[([0-9]+\.[0-9]+)\]'),
        ('size', r'([1-9][0-9]*) bytes'),
        ('url', r'from ([-a-zA-Z0-9@:%._\+~#=]{1,256}\.[a-zA-Z0-9()]{1,6}\b([-a-zA-Z0-9()@:%_\+.~#?&\/=]*)?)'),
        ('ip', r'\(\b((25[0-5]|2[0-4][0-9]|1[0-9][0-9]|[1-9]?[0-9])\.(25[0-5]|2[0-4][0-9]|1[0-9][0-9]|[1-9]?[0-9])\.(25[0-5]|2[0-4][0-9]|1[0-9][0-9]|[1-9]?[0-9])\.(25[0-5]|2[0-4][0-9]|1[0-9][0-9]|[1-9]?[0-9]))\b\)'),
        ('icmp_seq', r'icmp_seq=([1-9][0-9]*)'),
        ('ttl', r'ttl=([0-9]|[1-9][0-9]*)'),
        ('time', r'time=([0-9]|[1-9][0-9]*(\.[0-9]+)?) ms')]
for line in file_content:
    values = OrderedDict()
    if line:
        for (name, regex) in reg:
            obj = re.findall(regex, line)
            val = None
            if len(obj) :
                val = obj[0]
                if isinstance(val, tuple) and len(val) :
                    val = val[0]
            values[name] = val
        list.append(values)

In [13]:
raw_data = pd.DataFrame(list)
raw_data

timestamp  size                 url           ip icmp_seq ttl  \
0      1421761682.052172   665  lig-publig.imag.fr  129.88.11.7        1   6   
1      1421761682.277315  1373  lig-publig.imag.fr  129.88.11.7        1   6   
2      1421761682.502054   262  lig-publig.imag.fr  129.88.11.7        1   6   
3      1421761682.729257  1107  lig-publig.imag.fr  129.88.11.7        1   6   
4      1421761682.934648  1128  lig-publig.imag.fr  129.88.11.7        1   6   
5      1421761683.160397   489  lig-publig.imag.fr  129.88.11.7        1   6   
6      1421761683.443055  1759  lig-publig.imag.fr  129.88.11.7        1   6   
7      1421761683.672157  1146  lig-publig.imag.fr  129.88.11.7        1   6   
8      1421761683.899933   884  lig-publig.imag.fr  129.88.11.7        1   6   
9      1421761684.122687  1422  lig-publig.imag.fr  129.88.11.7        1   6   
10     1421761684.344135  1180  lig-publig.imag.fr  129.88.11.7        1   6   
11     1421761684.566271   999  lig-publig.imag.fr  129.88.11.7        1   6   
12     1421761684.770828    21  lig-publig.imag.fr  129.88.11.7        1   6   
13     1421761684.998504  1020  lig-publig.imag.fr  129.88.11.7        1   6   
14     1421761685.205172    71  lig-publig.imag.fr  129.88.11.7        1   6   
15     1421761685.414106    34  lig-publig.imag.fr  129.88.11.7        1   6   
16     1421761685.620117  1843  lig-publig.imag.fr  129.88.11.7        1   6   
17     1421761685.824949   407  lig-publig.imag.fr  129.88.11.7        1   6   
18     1421761686.029177   356  lig-publig.imag.fr  129.88.11.7        1   6   
19     1421761686.234464  1511  lig-publig.imag.fr  129.88.11.7        1   6   
20     1421761686.438772   587  lig-publig.imag.fr  129.88.11.7        1   6   
21     1421761686.643208   809  lig-publig.imag.fr  129.88.11.7        1   6   
22     1421761686.848323  1364  lig-publig.imag.fr  129.88.11.7        1   6   
23     1421761687.053400  1153  lig-publig.imag.fr  129.88.11.7        1   6   
24     1421761687.257704   853  lig-publig.imag.fr  129.88.11.7        1   6   
25     1421761687.463275  1510  lig-publig.imag.fr  129.88.11.7        1   6   
26     1421761687.668423   123  lig-publig.imag.fr  129.88.11.7        1   6   
27     1421761687.874230  1966  lig-publig.imag.fr  129.88.11.7        1   6   
28     1421761688.078667   933  lig-publig.imag.fr  129.88.11.7        1   6   
29     1421761688.283655   922  lig-publig.imag.fr  129.88.11.7        1   6   
...                  ...   ...                 ...          ...      ...  ..   
44383  1421771180.743715  1772  lig-publig.imag.fr  129.88.11.7        1   6   
44384  1421771180.949053    41  lig-publig.imag.fr  129.88.11.7        1   6   
44385  1421771181.155685  1944  lig-publig.imag.fr  129.88.11.7        1   6   
44386  1421771181.362095   400  lig-publig.imag.fr  129.88.11.7        1   6   
44387  1421771181.569409   226  lig-publig.imag.fr  129.88.11.7        1   6   
44388  1421771181.780805   466  lig-publig.imag.fr  129.88.11.7        1   6   
44389  1421771181.998869   350  lig-publig.imag.fr  129.88.11.7        1   6   
44390  1421771182.248969  1829  lig-publig.imag.fr  129.88.11.7        1   6   
44391  1421771182.512386  1954  lig-publig.imag.fr  129.88.11.7        1   6   
44392  1421771182.717961  1074  lig-publig.imag.fr  129.88.11.7        1   6   
44393  1421771182.923292    46  lig-publig.imag.fr  129.88.11.7        1   6   
44394  1421771183.129965  1844  lig-publig.imag.fr  129.88.11.7        1   6   
44395  1421771183.335449   645  lig-publig.imag.fr  129.88.11.7        1   6   
44396  1421771183.540901   444  lig-publig.imag.fr  129.88.11.7        1   6   
44397  1421771183.747983  1940  lig-publig.imag.fr  129.88.11.7        1   6   
44398  1421771183.954099  1411  lig-publig.imag.fr  129.88.11.7        1   6   
44399  1421771184.159879    49  lig-publig.imag.fr  129.88.11.7        1   6   
44400  1421771184.365815   420  lig-publig.imag.fr  129.88.11.7        1   6   
44401  14217711

In [15]:
raw_data[raw_data.isnull().any(axis=1)]

timestamp size                 url           ip icmp_seq ttl  \
12     1421761684.770828   21  lig-publig.imag.fr  129.88.11.7        1   6   
116    1421761706.146320    9  lig-publig.imag.fr  129.88.11.7        1   6   
314    1421761748.647974    9  lig-publig.imag.fr  129.88.11.7        1   6   
508    1421761788.500516    9  lig-publig.imag.fr  129.88.11.7        1   6   
590    1421761805.331125   18  lig-publig.imag.fr  129.88.11.7        1   6   
647    1421761817.308839   18  lig-publig.imag.fr  129.88.11.7        1   6   
1087   1421761907.694059   18  lig-publig.imag.fr  129.88.11.7        1   6   
1091   1421761908.512826   13  lig-publig.imag.fr  129.88.11.7        1   6   
1131   1421761916.713419   20  lig-publig.imag.fr  129.88.11.7        1   6   
1153   1421761921.229704   21  lig-publig.imag.fr  129.88.11.7        1   6   
1350   1421761962.174859   15  lig-publig.imag.fr  129.88.11.7        1   6   
1542   1421762001.590195   17  lig-publig.imag.fr  129.88.11.7        1   6   
1691   1421762032.199394   19  lig-publig.imag.fr  129.88.11.7        1   6   
1765   1421762047.397821    9  lig-publig.imag.fr  129.88.11.7        1   6   
1957   1421762088.369820   21  lig-publig.imag.fr  129.88.11.7        1   6   
2099   1421762117.516869    8  lig-publig.imag.fr  129.88.11.7        1   6   
2182   1421762134.551193   23  lig-publig.imag.fr  129.88.11.7        1   6   
2209   1421762140.101009   10  lig-publig.imag.fr  129.88.11.7        1   6   
2455   1421762191.278531   21  lig-publig.imag.fr  129.88.11.7        1   6   
2478   1421762196.022695   16  lig-publig.imag.fr  129.88.11.7        1   6   
2722   1421762246.169992   19  lig-publig.imag.fr  129.88.11.7        1   6   
2734   1421762248.634005   21  lig-publig.imag.fr  129.88.11.7        1   6   
3042   1421762311.874238   10  lig-publig.imag.fr  129.88.11.7        1   6   
3064   1421762316.560968    9  lig-publig.imag.fr  129.88.11.7        1   6   
3185   1421762342.293065   22  lig-publig.imag.fr  129.88.11.7        1   6   
3222   1421762349.889838   10  lig-publig.imag.fr  129.88.11.7        1   6   
3318   1421762369.740243   10  lig-publig.imag.fr  129.88.11.7        1   6   
3333   1421762372.892510   10  lig-publig.imag.fr  129.88.11.7        1   6   
3494   1421762406.232258    8  lig-publig.imag.fr  129.88.11.7        1   6   
3689   1421762447.771797    9  lig-publig.imag.fr  129.88.11.7        1   6   
...                  ...  ...                 ...          ...      ...  ..   
39760  1421770202.098919   14  lig-publig.imag.fr  129.88.11.7        1   6   
39929  1421770236.857197   22  lig-publig.imag.fr  129.88.11.7        1   6   
40039  1421770260.878994   22  lig-publig.imag.fr  129.88.11.7        1   6   
40398  1421770347.170294   12  lig-publig.imag.fr  129.88.11.7        1   6   
40659  1421770401.425936    8  lig-publig.imag.fr  129.88.11.7        1   6   
40704  1421770410.677288   20  lig-publig.imag.fr  129.88.11.7        1   6   
40882  1421770447.286588   15  lig-publig.imag.fr  129.88.11.7        1   6   
41276  1421770528.785624   12  lig-publig.imag.fr  129.88.11.7        1   6   
41421  1421770558.624793   16  lig-publig.imag.fr  129.88.11.7        1   6   
41494  1421770573.778775   22  lig-publig.imag.fr  129.88.11.7        1   6   
41689  1421770614.039516   15  lig-publig.imag.fr  129.88.11.7        1   6   
41833  1421770643.752354   17  lig-publig.imag.fr  129.88.11.7        1   6   
42094  1421770697.673096   10  lig-publig.imag.fr  129.88.11.7        1   6   
42119  1421770702.820645   21  lig-publig.imag.fr  129.88.11.7        1   6   
42165  1421770712.292955   18  lig-publig.imag.fr  129.88.11.7        1   6   
42171  1421770713.526885    9  lig-publig.imag.fr  129.88.11.7        1   6   
42216  1421770722.770927   17  lig-publig.imag.fr  129.88.11.7        1   6   
42290  1421770737.986337   17  lig-publig.imag.fr  129.88.11.7        1   6   
42391  1421770758.905166   17  lig-publig.imag.fr  129.88.11.7   

In [16]:
data = raw_data.dropna().copy()
data

timestamp  size                 url           ip icmp_seq ttl  \
0      1421761682.052172   665  lig-publig.imag.fr  129.88.11.7        1   6   
1      1421761682.277315  1373  lig-publig.imag.fr  129.88.11.7        1   6   
2      1421761682.502054   262  lig-publig.imag.fr  129.88.11.7        1   6   
3      1421761682.729257  1107  lig-publig.imag.fr  129.88.11.7        1   6   
4      1421761682.934648  1128  lig-publig.imag.fr  129.88.11.7        1   6   
5      1421761683.160397   489  lig-publig.imag.fr  129.88.11.7        1   6   
6      1421761683.443055  1759  lig-publig.imag.fr  129.88.11.7        1   6   
7      1421761683.672157  1146  lig-publig.imag.fr  129.88.11.7        1   6   
8      1421761683.899933   884  lig-publig.imag.fr  129.88.11.7        1   6   
9      1421761684.122687  1422  lig-publig.imag.fr  129.88.11.7        1   6   
10     1421761684.344135  1180  lig-publig.imag.fr  129.88.11.7        1   6   
11     1421761684.566271   999  lig-publig.imag.fr  129.88.11.7        1   6   
13     1421761684.998504  1020  lig-publig.imag.fr  129.88.11.7        1   6   
14     1421761685.205172    71  lig-publig.imag.fr  129.88.11.7        1   6   
15     1421761685.414106    34  lig-publig.imag.fr  129.88.11.7        1   6   
16     1421761685.620117  1843  lig-publig.imag.fr  129.88.11.7        1   6   
17     1421761685.824949   407  lig-publig.imag.fr  129.88.11.7        1   6   
18     1421761686.029177   356  lig-publig.imag.fr  129.88.11.7        1   6   
19     1421761686.234464  1511  lig-publig.imag.fr  129.88.11.7        1   6   
20     1421761686.438772   587  lig-publig.imag.fr  129.88.11.7        1   6   
21     1421761686.643208   809  lig-publig.imag.fr  129.88.11.7        1   6   
22     1421761686.848323  1364  lig-publig.imag.fr  129.88.11.7        1   6   
23     1421761687.053400  1153  lig-publig.imag.fr  129.88.11.7        1   6   
24     1421761687.257704   853  lig-publig.imag.fr  129.88.11.7        1   6   
25     1421761687.463275  1510  lig-publig.imag.fr  129.88.11.7        1   6   
26     1421761687.668423   123  lig-publig.imag.fr  129.88.11.7        1   6   
27     1421761687.874230  1966  lig-publig.imag.fr  129.88.11.7        1   6   
28     1421761688.078667   933  lig-publig.imag.fr  129.88.11.7        1   6   
29     1421761688.283655   922  lig-publig.imag.fr  129.88.11.7        1   6   
30     1421761688.488688    24  lig-publig.imag.fr  129.88.11.7        1   6   
...                  ...   ...                 ...          ...      ...  ..   
44383  1421771180.743715  1772  lig-publig.imag.fr  129.88.11.7        1   6   
44384  1421771180.949053    41  lig-publig.imag.fr  129.88.11.7        1   6   
44385  1421771181.155685  1944  lig-publig.imag.fr  129.88.11.7        1   6   
44386  1421771181.362095   400  lig-publig.imag.fr  129.88.11.7        1   6   
44387  1421771181.569409   226  lig-publig.imag.fr  129.88.11.7        1   6   
44388  1421771181.780805   466  lig-publig.imag.fr  129.88.11.7        1   6   
44389  1421771181.998869   350  lig-publig.imag.fr  129.88.11.7        1   6   
44390  1421771182.248969  1829  lig-publig.imag.fr  129.88.11.7        1   6   
44391  1421771182.512386  1954  lig-publig.imag.fr  129.88.11.7        1   6   
44392  1421771182.717961  1074  lig-publig.imag.fr  129.88.11.7        1   6   
44393  1421771182.923292    46  lig-publig.imag.fr  129.88.11.7        1   6   
44394  1421771183.129965  1844  lig-publig.imag.fr  129.88.11.7        1   6   
44395  1421771183.335449   645  lig-publig.imag.fr  129.88.11.7        1   6   
44396  1421771183.540901   444  lig-publig.imag.fr  129.88.11.7        1   6   
44397  1421771183.747983  1940  lig-publig.imag.fr  129.88.11.7        1   6   
44398  1421771183.954099  1411  lig-publig.imag.fr  129.88.11.7        1   6   
44399  1421771184.159879    49  lig-publig.imag.fr  129.88.11.7        1   6   
44400  1421771184.365815   420  lig-publig.imag.fr  129.88.11.7        1   6   
44401  14217711